In [62]:
import pandas as pd
import json
import copy

# GOAL

- make a comparaison of evaluation on different methods of smoothing results. 
- using ground truth and actual classification.

For each taxon rank I need to:
- Select a cropped image. 
- I compare this to the ground truth.
- If it's the same, in the evaluation column, I may put Correct or 1. 0 if it's not the same.

Then I count the correct / total, that's my accuracy.  

I redo the same thing but with the - In the best label, based on smoothing strategies.

# Create Dataset

In [57]:
def from_json_to_df(json_file_path):
    """
    Convert the classification json file into a simple and usable dataframe. 
    We remove the key "species count" because it is useless here.
    Then to extract specific information of classification you can do df['000001.jpg']['track_info'] and then select the image
    """
    with open(json_file_path) as f:
        d = json.load(f)
        del d['species_count'] 
    return pd.DataFrame.from_dict(d,orient='index')

In [61]:
csv_file_path = "../../0_database/tracking/inat_validation_data_with_sources_and_scores-20230204.csv" # contains the ground truth result for each cropped image
json_file_path = '../../0_database/tracking/set2_maxim-kent.json' # contains the classification result for each cropped image
df_gt = pd.read_csv(csv_file_path)
df_classification = from_json_to_df(json_file_path)
# df_evaluation = pd.DataFrame(columns=['source_image_cropped', 'ground_truth_taxon_rank', 'ground_truth_taxon_name','prediction_made','confidence_score','evaluation']) # will contain the accuracy without smoothing
# df_evaluation_smoothing_max = pd.DataFrame(columns=['source_image_cropped', 'ground_truth_taxon_rank', 'ground_truth_taxon_name','prediction_made','confidence_score','evaluation']) # will contain the accuracy with smoothing based on max score
# df_evaluation_smoothing_most_frequent = pd.DataFrame(columns=['source_image_cropped', 'ground_truth_taxon_rank', 'ground_truth_taxon_name','prediction_made','confidence_score','evaluation']) # will contain the accuracy  with smoothing based on most frequent score
# df_evaluation_smoothing_average = pd.DataFrame(columns=['source_image_cropped', 'ground_truth_taxon_rank', 'ground_truth_taxon_name','prediction_made','confidence_score','evaluation']) # will contain the accuracy  with smoothing based on max average score

In [60]:
display(df_gt.head(2))
display(df_classification.head())

inat_id                                        description  \
0  142101810  Machine capture. Cropped image: 000001.jpg. So...   
1  142101812  Machine capture. Cropped image: 000002.jpg. So...   

      source_image_original source_image_cropped    status        date  \
0  20220731233507-00-91.jpg           000001.jpg  needs_id  2022-07-31   
1  20220731233507-00-91.jpg           000002.jpg  needs_id  2022-07-31   

                   timestamp  identifications_most_agree   taxon_name  \
0  2022-08-01 03:35:00+00:00                        True     Pandemis   
1  2022-08-01 03:35:00+00:00                        True  Olethreutes   

  taxon_rank  ...  true_label_rank   true_label                  label_aug22  \
0      genus  ...            genus     Pandemis  Argyrotaenia quadrifasciana   
1      genus  ...            genus  Olethreutes                Grammia virgo   

  score_aug22               label_mixedres score_mixedres correct_aug22  \
0          31  Argyrotaenia quadrifasciana             66         False   
1          54                Grammia virgo             65         False   

  correct_mixedres                                        model_aug22  \
0            False  quebec-vermont-moth-model_v02_efficientnetv2-b...   
1            False  quebec-vermont-moth-model_v02_efficientnetv2-b...   

                                      model_mixedres  
0  quebec-vermont-moth-model_v07_resnet50_2022-12...  
1  quebec-vermont-moth-model_v07_resnet50_2022-12...  

[2 rows x 25 columns]

region        date  track_id  \
000001.jpg  Quebec  2022_07_31       2.0   
000002.jpg  Quebec  2022_07_31       3.0   
000003.jpg  Quebec  2022_07_31       4.0   
000004.jpg  Quebec  2022_07_31       6.0   
000005.jpg  Quebec  2022_07_31       7.0   

                                                   prediction  \
000001.jpg  [[Choristoneura parallela, 29], [Argyrotaenia ...   
000002.jpg  [[Grammia virguncula, 33], [Martyringa latipen...   
000003.jpg  [[Idia denticulalis, 31], [Metalectra discalis...   
000004.jpg  [[Agonopterix robiniella, 23], [Crambidia pall...   
000005.jpg  [[Archips cerasivorana, 25], [Rhynchagrotis cu...   

                                                   track_info  
000001.jpg  [[20220731233507-00-91.jpg, 2432, 1485, 2566, ...  
000002.jpg  [[20220731233507-00-91.jpg, 3389, 1064, 3522, ...  
000003.jpg  [[20220731233507-00-91.jpg, 600, 287, 751, 449...  
000004.jpg  [[20220731233507-00-91.jpg, 1689, 740, 1780, 8...  
000005.jpg  [[20220731233507-00-91.jpg, 3482, 2052, 3649, ...

In [110]:
def smoothing_max_value(list_results):
    # ex: [['20220731233507-00-91.jpg', 2432, 1485, 2566, 1642, 'Choristoneura parallela', 29], ['20220731232026-00-79.jpg', 1650, 1277, 1768, 1448, 'Archips argyrospila', 39]]
    df = pd.DataFrame(list_results, columns = ['img', 'x1', 'x2', 'y1', 'y2', 'label', 'confidence'])
    #display(df)
    max_confidence_score = df["confidence"].max()
    max_confidence_index = df["confidence"].idxmax()
    new_label = df.iloc[max_confidence_index, df.columns.get_loc("label")]
    #print(max_confidence_index, max_confidence_score, new_label)
    return max_confidence_score, new_label

In [114]:
def create_df_evaluation(df_gt,df_classification):
    df_evaluation = pd.DataFrame.copy(df_classification)
    # test = df_evaluation.loc['000001.jpg']['track_info']
    # smoothing_max_value(test)
    smoothing_labels = []
    scores = []
    for row in df_evaluation['track_info']:
        score, label = smoothing_max_value(row)
        scores.append(score)
        smoothing_labels.append(label)
    df_evaluation['smoothing_label'] = smoothing_labels
    df_evaluation['score'] = scores
    return df_evaluation

In [119]:
df_evaluation = create_df_evaluation(df_gt,df_classification)

img    x1    x2    y1    y2                    label  \
0  20220731233507-00-91.jpg  2432  1485  2566  1642  Choristoneura parallela   
1  20220731232026-00-79.jpg  1650  1277  1768  1448      Archips argyrospila   

   confidence  
0          29  
1          39

1 39 Archips argyrospila


img    x1    x2    y1    y2               label  \
0  20220731233507-00-91.jpg  3389  1064  3522  1230  Grammia virguncula   
1  20220731232026-00-79.jpg  3254  1412  3443  1577    Holomelina laeta   

   confidence  
0          33  
1          36

1 36 Holomelina laeta


img   x1   x2   y1   y2              label  confidence
0  20220731233507-00-91.jpg  600  287  751  449  Idia denticulalis          31

...

8 99 Hypoprepia fucosa


img    x1    x2    y1    y2  \
0   20220802024638-00-52.jpg   430   247   537   365   
1   20220802024742-00-52.jpg  3682   431  3773   575   
2   20220802024825-00-52.jpg  3633   129  3735   260   
3   20220802024724-00-52.jpg  1568     0  1654   168   
4   20220802024554-00-52.jpg  3759  1282  3855  1438   
5   20220802024643-00-52.jpg  2647   902  2751  1021   
6   20220802024559-00-52.jpg  3317  1122  3422  1265   
7   20220802024647-00-52.jpg  1568     0  1654   169   
8   20220802024616-00-52.jpg  2928   205  3023   320   
9   20220802024609-00-52.jpg  2928   201  3025   323   
10  20220802024524-00-52.jpg  2218   599  2302   756   
11  20220802024515-00-52.jpg  2212   603  2313   765   
12  20220802024544-00-52.jpg  2216   598  2298   754   
13  20220802024539-00-52.jpg  2217   599  2300   755   
14  20220802024534-00-52.jpg  2217   600  2303   757   
15  20220802024645-00-52.jpg  1567     0  1653   165   
16  20220802024549-00-52.jpg  1607   601  1689   734   
17  20220802024443-00-52.jpg  1620   648  1696   868   
18  20220802024502-00-52.jpg  1607   602  1688   732   
19  20220802024529-00-52.jpg  1607   601  1689   733   
20  20220802024532-00-52.jpg  1606   598  1693   734   
21  20220802024511-00-52.jpg  1577   601  1687   752   
22  20220802024452-00-52.jpg  1619   648  1697   867   
23  20220802024520-00-52.jpg  1606   601  1689   733   
24  20220802024627-00-52.jpg  1604   602  1693   732   
25  20220802024429-00-52.jpg  1615   648  1684   781   
26  20220802024448-00-52.jpg  1617   649  1696   868   
27  20220802024434-00-52.jpg  1614   647  1685   781   
28  20220802024401-00-52.jpg  1612   695  1707   813   
29  20220802024413-00-52.jpg  1616   650  1683   779   
30  20220802024406-00-52.jpg  1610   693  1708   813   
31  20220802024427-00-52.jpg  1609   646  1684   779   
32  20220802024457-00-52.jpg  1606   601  1688   733   
33  20220802024622-00-52.jpg  1607   601  1691   733   
34  20220802024422-00-52.jpg  1611   646  1686   781   
35  20220802024408-00-52.jpg  1610   691  1708   814   
36  20220802024624-00-52.jpg  1606   598  1692   734   
37  20220802024415-00-52.jpg  1611   646  1736   779   
38  20220802024418-00-52.jpg  1615   652  1683   779   
39  20220802024411-00-52.jpg  1610   693  1708   814   
40  20220802024342-00-52.jpg  1633   708  1702   837   
41  20220802024356-00-52.jpg  1612   694  1708   814   
42  20220802024632-00-52.jpg  1607   601  1690   733   
43  20220802024604-00-52.jpg  1607   599  1692   735   
44  20220802024317-00-52.jpg  1975   533  2095   685   
45  20220802024432-00-52.jpg   875   622   985   786   
46  20220802024312-00-52.jpg   881   735   977   887   
47  20220802024506-00-52.jpg   877   623   981   782   
48  20220802024329-00-52.jpg  1612   362  1687   487   
49  20220802024336-00-52.jpg  1615   366  1687   487   

                          label  confidence  
0        Eufidonia discospilata          15  
1       Sparganothis tristriata          19  
2            Lygropia rivulalis          69  
3           Endothenia hebesana          13  
4    Argyrotaenia quercifoliana          54  
5                Haploa confusa          28  
6       Polygrammate hebraeicum          35  
7            Cydia latiferreana          22  
8            Lygropia rivulalis          78  
9            Lygropia rivulalis          35  
10           Lygropia rivulalis          40  
11           Lygropia rivulalis          37  
12           Lygropia rivulalis          24  
13      Polygrammate hebraeicum          38  
14           Lygropia rivulalis          57  
15           Cydia latiferreana          42  
16          Archips argyrospila          78  
17           Lygropia rivulalis          27  
18          Archips argyrospila          57  
19          Archips argyrospila          31  
20          Archips argyrospila          43  
21          Choristoneura pinus          62  
22        Martyringa latipennis          26  
23          Archips argyrospila          86  
24          Archip

44 94 Lygropia rivulalis


img    x1    x2    y1    y2  \
0   20220802024638-00-52.jpg   244   106   315   222   
1   20220802024742-00-52.jpg  1929  1813  2020  1918   
2   20220802024825-00-52.jpg  1794  1893  1891  2001   
3   20220802024724-00-52.jpg  1603  1581  1692  1712   
4   20220802024554-00-52.jpg  1607   601  1689   734   
5   20220802024643-00-52.jpg  1596  1583  1686  1713   
6   20220802024559-00-52.jpg  1595  1582  1684  1715   
7   20220802024647-00-52.jpg  1596  1584  1687  1714   
8   20220802024616-00-52.jpg  1600  1581  1687  1711   
9   20220802024609-00-52.jpg  1020   961  1108  1076   
10  20220802024524-00-52.jpg   866  1303   939  1415   
11  20220802024515-00-52.jpg   867  1302   939  1415   
12  20220802024544-00-52.jpg   867  1303   944  1414   
13  20220802024539-00-52.jpg   865  1302   939  1415   
14  20220802024534-00-52.jpg   866  1303   939  1415   
15  20220802024645-00-52.jpg   824  1297   923  1445   
16  20220802024549-00-52.jpg   867  1302   939  1415   
17  20220802024443-00-52.jpg   533  1024   626  1176   
18  20220802024502-00-52.jpg   595   354   709   527   
19  20220802024529-00-52.jpg  2580  2000  2709  2127   
20  20220802024532-00-52.jpg  2700  1976  2859  2145   
21  20220802024511-00-52.jpg  3026     2  3165   141   

                         label  confidence  
0        Martyringa latipennis          31  
1             Anania hortulata          47  
2      Polygrammate hebraeicum          24  
3      Argyrotaenia alisellana          16  
4           Lygropia rivulalis          13  
5   Argyrotaenia quercifoliana          38  
6   Argyrotaenia quercifoliana          64  
7   Argyrotaenia quercifoliana          71  
8            Crambidia pallida          51  
9      Polygrammate hebraeicum          43  
10          Grammia virguncula          31  
11  Neocataclysta magnificalis          21  
12         Elophila ekthlipsis          25  
13        Parapoynx badiusalis          30  
14        Parapoynx badiusalis          58  
15     Harrisimemna trisignata          94  
16          Grammia virguncula          26  
17      Agonopterix robiniella          34  
18  Argyrotaenia quercifoliana          52  
19         Marathyssa inficita          29  
20         Phobetron pithecium          49  
21     Agriphila vulgivagellus          33

15 94 Harrisimemna trisignata


In [120]:
display(df_evaluation)

region        date  track_id  \
000001.jpg  Quebec  2022_07_31       2.0   
000002.jpg  Quebec  2022_07_31       3.0   
000003.jpg  Quebec  2022_07_31       4.0   
000004.jpg  Quebec  2022_07_31       6.0   
000005.jpg  Quebec  2022_07_31       7.0   
...            ...         ...       ...   
000996.jpg  Quebec  2022_08_02     132.0   
000997.jpg  Quebec  2022_08_02     131.0   
000998.jpg  Quebec  2022_08_02     134.0   
000999.jpg  Quebec  2022_08_02     137.0   
001000.jpg  Quebec  2022_08_02     140.0   

                                                   prediction  \
000001.jpg  [[Choristoneura parallela, 29], [Argyrotaenia ...   
000002.jpg  [[Grammia virguncula, 33], [Martyringa latipen...   
000003.jpg  [[Idia denticulalis, 31], [Metalectra discalis...   
000004.jpg  [[Agonopterix robiniella, 23], [Crambidia pall...   
000005.jpg  [[Archips cerasivorana, 25], [Rhynchagrotis cu...   
...                                                       ...   
000996.jpg  [[Dioryctria disclusa, 21], [Acleris albicoman...   
000997.jpg  [[Phaeoura quernaria, 38], [Thyris maculata, 1...   
000998.jpg  [[Macaria granitata, 26], [Harrisimemna trisig...   
000999.jpg  [[Eufidonia discospilata, 15], [Epelis truncat...   
001000.jpg  [[Martyringa latipennis, 31], [Grammia virgunc...   

                                                   track_info  \
000001.jpg  [[20220731233507-00-91.jpg, 2432, 1485, 2566, ...   
000002.jpg  [[20220731233507-00-91.jpg, 3389, 1064, 3522, ...   
000003.jpg  [[20220731233507-00-91.jpg, 600, 287, 751, 449...   
000004.jpg  [[20220731233507-00-91.jpg, 1689, 740, 1780, 8...   
000005.jpg  [[20220731233507-00-91.jpg, 3482, 2052, 3649, ...   
...                                                       ...   
000996.jpg  [[20220802024729-00-52.jpg, 3737, 1790, 3859, ...   
000997.jpg  [[20220802024801-00-52.jpg, 1896, 978, 2237, 1...   
000998.jpg  [[20220802024638-00-52.jpg, 1295, 1285, 1543, ...   
000999.jpg  [[20220802024638-00-52.jpg, 430, 247, 537, 365...   
001000.jpg  [[20220802024638-00-52.jpg, 244, 106, 315, 222...   

                    smoothing_label  score  
000001.jpg      Archips argyrospila     39  
000002.jpg         Holomelina laeta     36  
000003.jpg        Idia denticulalis     31  
000004.jpg       Cydia latiferreana     94  
000005.jpg   Agonopterix robiniella     61  
...                             ...    ...  
000996.jpg      Dioryctria disclusa     21  
000997.jpg       Phaeoura quernaria     38  
000998.jpg        Hypoprepia fucosa     99  
000999.jpg       Lygropia rivulalis     94  
001000.jpg  Harrisimemna trisignata     94  

[1000 rows x 7 columns]